In [ ]:
pip install yfinance

In [ ]:
import requests
from bs4 import BeautifulSoup
import re
import pandas as pd
import nltk
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from matplotlib import pyplot as plt
import yfinance as yf

In [ ]:
nltk.download('vader_lexicon')

[nltk_data] Downloading package vader_lexicon to /root/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


True

In [ ]:
def generate_cnbc_url(urls, years):
  header = 'https://www.cnbc.com/site-map/articles/'

  # invalid dates will just have empty requests, inconsequential to runtime
  months = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December']
  days = range(1,32)

  # all article links have this form followed by date and article name
  target = 'https://www.cnbc.com/20'

  for year in years:
    for i in range(len(months)):
      for day in days:
        date = year + '-' + str(i + 1).zfill(2) + '-' + str(day).zfill(2)
        datetext = year + '/' + months[i] + '/' + str(day) + '/' 
        url = header + datetext
        reqs = requests.get(url)
        soup = BeautifulSoup(reqs.text, 'html.parser')

        urls[date] = []

        # grabs all hyperlinks from page
        for link in soup.find_all('a'):
          check = link.get('href')
          if target in check:
            urls[date].append(check)
  
  return urls

In [ ]:
# removes () from company names and removes duplicate mentions
def clean_company_lst(companies):
  companies.sort()
  cleaned = []
  for x in companies:
    x = x[1:len(x)-1]
    if (not cleaned or cleaned[-1] != x):
      cleaned.append(x)

  return cleaned

In [ ]:
# computes the sentiment score for an article from cnbc
def cnbc_url_sentiment(url, date, sentiment_scores, target_companies, target_index):
  reqs = requests.get(url)
  soup = BeautifulSoup(reqs.text, 'html.parser')
  sections = []
  alt_names = {}
  for element in soup.find_all(class_='group'):
    for each in element.find_all('p'):
      sections.append(each)
      for link in each.find_all('a'):
        check = re.search(r'/quotes/[A-Z]+', link.get('href'))
        if (check):
          c = check.group(0)[8:]
          alt_names[link.get_text()] = c

  # measures sentiment for each paragraph in article
  for each in sections:
    paragraph = each.get_text()
    # companies are typically of the form (XYZ)
    companies = re.findall(r'\([A-Z]+\)', paragraph)
    companies = clean_company_lst(companies)

    # some companies are referred to by name
    for name in alt_names.keys():
      if (alt_names[name] not in companies and name in paragraph):
        companies.append(alt_names[name])

    # only focuses on target companies
    comp_filtered = set(companies).intersection(set(target_companies))

    # ignores paragraphs that don't mention companies, since they don't affect how sentiment is calculated
    if (comp_filtered):
      sentiment = vader.polarity_scores(paragraph)['compound']

      for c in comp_filtered:
        sentiment_scores.at[target_index[c], 'Sentiment'] += sentiment
        sentiment_scores.at[target_index[c], 'Total Mentions'] += 1
  
  return sentiment_scores

In [ ]:
vader = SentimentIntensityAnalyzer()

In [ ]:
# urls dictionary that is built in call to generate_cnbc_url
urls = {}

In [ ]:
sentiment_scores_2019 = pd.DataFrame(columns={'Company':[], 'Date':[], 'Sentiment':[], 'Total Mentions':[]})

In [ ]:
sentiment_scores_2020 = pd.DataFrame(columns={'Company':[], 'Date':[], 'Sentiment':[], 'Total Mentions':[]})

In [ ]:
sentiment_scores_2021 = pd.DataFrame(columns={'Company':[], 'Date':[], 'Sentiment':[], 'Total Mentions':[]})

In [ ]:
years = ['2020']
target_companies = ['GME', 'TSLA', 'S&P500']

In [ ]:
generate_cnbc_url(urls, years)

{'2019-01-01': ['https://www.cnbc.com/2018/12/20/michael-phelps-strategy-for-reaching-his-goals.html',
  'https://www.cnbc.com/2018/12/21/twitter-square--books-everyone-should-read-in-2019.html',
  'https://www.cnbc.com/2018/12/20/suzy-welch-the-new-years-resolution-that-can-supercharge-your-career.html',
  'https://www.cnbc.com/2019/01/01/trump-invites-congressional-leaders-to-meet-about-government-shutdown.html',
  'https://www.cnbc.com/2018/12/31/here-are-some-of-the-winners-in-retail-heading-into-2019-like-walmart.html',
  'https://www.cnbc.com/2018/12/31/bishop-stalls-hungover-how-to-cure-a-hangover.html',
  'https://www.cnbc.com/2018/12/31/chipotle-poised-for-best-year-since-2013-thanks-to-ceo-brian-niccol.html'],
 '2019-01-02': ['https://www.cnbc.com/2018/12/12/popular-us-cities-where-you-can-buy-a-home-on-a-60000-dollar-salary.html',
  'https://www.cnbc.com/2019/01/02/your-first-trade-for-wednesday-january-2.html',
  'https://www.cnbc.com/2019/01/02/asia-markets-us-china-trade-

In [ ]:
# generates cnbc sentiments for all urls for the target companies
def cnbc_sentiment(sentiment_scores, urls, target_companies):
  # target index is convenient for keeping track of index to modify dataframe
  target_index = {}
  for date in urls.keys():
    if (urls[date]):
      for company in target_companies:
        sentiment_scores.loc[len(sentiment_scores)]=[company, date, 0, 0]
        target_index[company] = len(sentiment_scores) - 1
    for url in urls[date]:
      cnbc_url_sentiment(url, date, sentiment_scores, target_companies, target_index)

In [ ]:
cnbc_sentiment(sentiment_scores_2020, urls, target_companies)

In [ ]:
sentiment_scores['Average Sentiment'] = sentiment_scores['Sentiment'] / sentiment_scores['Total Mentions']

In [ ]:
sentiment_scores.to_csv('cnbc2019.csv')